# Time-Based Cross-Validation Split Generation

**Author:** Daniel Costa  
**Project:** Flight Delay Prediction (W261 Final Project)  
**Dataset:** 5-Year Flight Data (2015-2019)

---

## Overview

This notebook generates **time-based cross-validation splits** for training neural network models on flight delay prediction. Time-based splitting is critical for time-series data to prevent data leakage—ensuring the model never trains on future information.

### Methodology

| Parameter | Value | Description |
|-----------|-------|-------------|
| Training Window | 30 days × 4 years | ~14,400 hours of training data per fold |
| Gap Size | 2 hours | Prevents label leakage at split boundary |
| Validation Window | 7 days × 4 years | ~3,360 hours of validation data per fold |
| Step Size | 85 hours × 4 years | Rolling window advancement |
| **Total Folds** | **10** | Sliding window cross-validation |

### Time-Based Split Visualization

```
Fold 1: [====== TRAIN (30d) ======][GAP][=== VAL (7d) ===]
Fold 2:      [====== TRAIN (30d) ======][GAP][=== VAL (7d) ===]
Fold 3:           [====== TRAIN (30d) ======][GAP][=== VAL (7d) ===]
...
Fold 10:                                    [====== TRAIN (30d) ======][GAP][=== VAL (7d) ===]
```

---

## Table of Contents

1. [Setup & Configuration](#setup)
2. [Data Loading](#data-loading)
3. [Time Index Creation](#time-index)
4. [Cross-Validation Split Generation](#cv-splits)
5. [Export Splits](#export)

In [0]:
# =============================================================================
# Section 1: Setup & Configuration
# =============================================================================

from pyspark.sql import functions as F
from pyspark.sql.window import Window

# -----------------------------------------------------------------------------
# Cross-Validation Configuration
# -----------------------------------------------------------------------------
# Time windows are multiplied by 4 to account for 4 years of data (2015-2019)
# This creates overlapping folds that span similar time periods across years

CV_CONFIG = {
    # Training window: 30 days worth of hours (720 hours × 4 years)
    "train_hours": 720 * 4 * 5,
    
    # Gap between train and validation to prevent label leakage
    "gap_hours": 2,
    
    # Validation window: 7 days worth of hours (168 hours × 4 years)
    "val_hours": 168 * 4 * 5,
    
    # Step size for sliding window (determines fold overlap)
    "step_hours": 85 * 4 * 5,
}

# Data paths
DATA_PATHS = {
    "train": "dbfs:/student-groups/Group_2_2/5_year_custom_joined/fe_graph_and_holiday_nnfeat/training_splits/train_w_preds.parquet/",
    "val": "dbfs:/student-groups/Group_2_2/5_year_custom_joined/fe_graph_and_holiday_nnfeat/training_splits/val_w_preds.parquet/",
    "test": "dbfs:/student-groups/Group_2_2/5_year_custom_joined/fe_graph_and_holiday_nnfeat/training_splits/test_w_preds.parquet/",
    "output": "dbfs:/student-groups/Group_2_2/5_year_custom_joined/fe_graph_and_holiday_nnfeat/cv_splits2",
}

# Flag to control whether to save (prevents accidental overwrites)
SAVE_SPLITS = False  # Set to True to enable saving

In [0]:
# =============================================================================
# Section 2: Data Loading
# =============================================================================

# Load feature-engineered datasets with graph features and holiday indicators
train_df = spark.read.parquet(DATA_PATHS["train"])
val_df = spark.read.parquet(DATA_PATHS["val"])
test_df = spark.read.parquet(DATA_PATHS["test"])

print(f"Training set:   {train_df.count():,} records")
print(f"Validation set: {val_df.count():,} records")
print(f"Test set:       {test_df.count():,} records")

In [0]:
# =============================================================================
# Section 3: Time Index Creation
# =============================================================================

# Combine train and validation sets for cross-validation
# (Test set is held out for final evaluation)
cv_df = train_df.unionByName(val_df)

# Calculate dataset start time for time indexing
min_timestamp = cv_df.agg(F.min("utc_timestamp")).collect()[0][0]
print(f"Dataset start time: {min_timestamp}")

# Create initial time index (hours since dataset start)
cv_df = cv_df.withColumn(
    "time_idx", 
    ((F.col("utc_timestamp").cast("long") - F.lit(min_timestamp).cast("long")) / 3600).cast("long")
)

Dataset start time: 2015-01-01 03:30:00


In [0]:
# Filter out cancelled flights (only predict delays for flights that departed)
cv_df = cv_df.filter(F.col("CANCELLED") != 1)

total_records = cv_df.count()
print(f"Total records after filtering cancelled flights: {total_records:,}")

# Preview the data
display(cv_df.limit(10))

22451084


flight_uid page_rank out_degree in_degree weighted_out_degree weighted_in_degree N_RUNWAYS betweenness_unweighted closeness betweenness avg_origin_dep_delay avg_dest_arr_delay avg_daily_route_flights avg_route_delay avg_hourly_flights QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK FL_DATE OP_UNIQUE_CARRIER OP_CARRIER_AIRLINE_ID OP_CARRIER TAIL_NUM OP_CARRIER_FL_NUM ORIGIN_AIRPORT_ID ORIGIN_AIRPORT_SEQ_ID ORIGIN_CITY_MARKET_ID ORIGIN ORIGIN_CITY_NAME ORIGIN_STATE_ABR ORIGIN_STATE_FIPS ORIGIN_STATE_NM ORIGIN_WAC DEST_AIRPORT_ID DEST_AIRPORT_SEQ_ID DEST_CITY_MARKET_ID DEST DEST_CITY_NAME DEST_STATE_ABR DEST_STATE_FIPS DEST_STATE_NM DEST_WAC CRS_DEP_TIME DEP_TIME DEP_DELAY DEP_DELAY_NEW DEP_DEL15 DEP_DELAY_GROUP DEP_TIME_BLK TAXI_OUT WHEELS_OFF WHEELS_ON TAXI_IN CRS_ARR_TIME ARR_TIME ARR_DELAY ARR_DELAY_NEW ARR_DEL15 ARR_DELAY_GROUP ARR_TIME_BLK CANCELLED CANCELLATION_CODE DIVERTED CRS_ELAPSED_TIME ACTUAL_ELAPSED_TIME AIR_TIME FLIGHTS DISTANCE DISTANCE_GROUP CARRIER_DELAY WEATHER_DELAY NAS_DELAY SECURITY_DELAY LATE_AIRCRAFT_DELAY FIRST_DEP_TIME TOTAL_ADD_GTIME LONGEST_ADD_GTIME DIV_AIRPORT_LANDINGS DIV_REACHED_DEST DIV_ACTUAL_ELAPSED_TIME DIV_ARR_DELAY DIV_DISTANCE DIV1_AIRPORT DIV1_AIRPORT_ID DIV1_AIRPORT_SEQ_ID DIV1_WHEELS_ON DIV1_TOTAL_GTIME DIV1_LONGEST_GTIME DIV1_WHEELS_OFF DIV1_TAIL_NUM DIV2_AIRPORT DIV2_AIRPORT_ID DIV2_AIRPORT_SEQ_ID DIV2_WHEELS_ON DIV2_TOTAL_GTIME DIV2_LONGEST_GTIME DIV2_WHEELS_OFF DIV2_TAIL_NUM DIV3_AIRPORT DIV3_AIRPORT_ID DIV3_AIRPORT_SEQ_ID DIV3_WHEELS_ON DIV3_TOTAL_GTIME DIV3_LONGEST_GTIME DIV3_WHEELS_OFF DIV3_TAIL_NUM DIV4_AIRPORT DIV4_AIRPORT_ID DIV4_AIRPORT_SEQ_ID DIV4_WHEELS_ON DIV4_TOTAL_GTIME DIV4_LONGEST_GTIME DIV4_WHEELS_OFF DIV4_TAIL_NUM DIV5_AIRPORT DIV5_AIRPORT_ID DIV5_AIRPORT_SEQ_ID DIV5_WHEELS_ON DIV5_TOTAL_GTIME DIV5_LONGEST_GTIME DIV5_WHEELS_OFF DIV5_TAIL_NUM year HourlyDryBulbTemperature HourlyDewPointTemperature HourlyRelativeHumidity HourlyAltimeterSetting HourlyVisibility HourlyStationPressure HourlyWetBulbTemperature HourlyPrecipitation HourlyCloudCoverage HourlyCloudElevation HourlyWindSpeed utc_timestamp CRS_DEP_MINUTES origin_delays_4h prev_flight_delay_in_minutes prev_flight_delay delay_origin_7d delay_origin_carrier_7d route delay_route_7d flight_count_24h LANDING_TIME_DIFF_MINUTES AVG_ARR_DELAY_ORIGIN AVG_TAXI_OUT_ORIGIN IS_HOLIDAY IS_HOLIDAY_WINDOW AIRPORT_HUB_CLASS RATING AIRLINE_CATEGORY dep_hour day_of_year dep_hour_sin dep_hour_cos dow_sin dow_cos doy_sin doy_cos HourlyVisibility_3h_change HourlyStationPressure_3h_change HourlyDryBulbTemperature_3h_change HourlyWindSpeed_3h_change HourlyPrecipitation_3h_change utc_ts_sec ground_flights_last_hour arrivals_last_hour xgb_predicted_delay time_idx ORD-2015-01-13-20398-3423-N671MQ-1335 7.49756322119521E60 180 180 746.4306808859722 745.0401968826907 8 0.14672145537968861 5.363030041286898E-4 0.29526462395543174 12.115997300701421 7.452488687782806 1.0910582444626744 10.829323308270677 0.2534864643150123 1 1 13 2 2015-01-13 MQ 20398 MQ N671MQ 3423 13930 1393003 30977 ORD Chicago, IL IL 17 Illinois 41 10268 1026802 30268 ALO Waterloo, IA IA 19 Iowa 61 1335 1507 92.0 92.0 1.0 6 1300-1359 16.0 1523 1605 5.0 1443 1610 87.0 87.0 1.0 5 1400-1459 0.0 null 0.0 68.0 63.0 42.0 1.0 234.0 1 8.0 0.0 0.0 0.0 79.0 null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2015 16.974967717280947 9.224738421862204 71.29865199427508 30.706512517903818 5.477475836012067 29.975729062205048 14.990760017021216 0.0 8.0 21.032402152263067 9.550120497587287 2015-01-13T13:35:00Z 815 45 64.0 1 187556.0 52706.0 ORD-ALO 1129.0 3 -6.083333333333333 41.92905253704535 22.834530758868432 0 0 0 2.8 2 13.583333333333334 13.0 -0.4027466898587371 -0.9153114791194472 0.9749279121818236 -0.22252093395631434 0.2219215130041655 0.9750645322571948 -8.881784197001252E-16 0.0 0.0 0.0 0.0 1421156100 69 0 5

In [0]:
# Reconstruct UTC timestamp from flight date and scheduled departure time
# CRS_DEP_TIME is in HHMM format (e.g., 1430 for 2:30 PM)
cv_df = cv_df.withColumn(
    "utc_timestamp",
    F.to_timestamp(
        F.concat(
            F.col("FL_DATE"),
            F.lit(" "),
            F.lpad(F.col("CRS_DEP_TIME").cast("string"), 4, "0")
        ),
        "yyyy-MM-dd HHmm"
    )
)

## Section 4: Cross-Validation Split Generation

The time index is created using `dense_rank()` over hourly-truncated timestamps. This ensures:
- Contiguous time indices (no gaps)
- Consistent ordering across the dataset
- Proper sliding window behavior for CV folds

In [0]:
# Truncate timestamp to hour level for consistent time bucketing
df_indexed = cv_df.withColumn(
    "hour", 
    F.date_trunc("hour", F.col("utc_timestamp"))
)

# Create dense time index based on unique hours
# dense_rank() ensures no gaps in the sequence
window_spec = Window.orderBy("hour")
df_indexed = df_indexed.withColumn(
    "time_idx", 
    F.dense_rank().over(window_spec)
)

print(f"Created time index with dense ranking")
display(df_indexed.select("FL_DATE", "CRS_DEP_TIME", "hour", "time_idx").limit(10))

flight_uid page_rank out_degree in_degree weighted_out_degree weighted_in_degree N_RUNWAYS betweenness_unweighted closeness betweenness avg_origin_dep_delay avg_dest_arr_delay avg_daily_route_flights avg_route_delay avg_hourly_flights QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK FL_DATE OP_UNIQUE_CARRIER OP_CARRIER_AIRLINE_ID OP_CARRIER TAIL_NUM OP_CARRIER_FL_NUM ORIGIN_AIRPORT_ID ORIGIN_AIRPORT_SEQ_ID ORIGIN_CITY_MARKET_ID ORIGIN ORIGIN_CITY_NAME ORIGIN_STATE_ABR ORIGIN_STATE_FIPS ORIGIN_STATE_NM ORIGIN_WAC DEST_AIRPORT_ID DEST_AIRPORT_SEQ_ID DEST_CITY_MARKET_ID DEST DEST_CITY_NAME DEST_STATE_ABR DEST_STATE_FIPS DEST_STATE_NM DEST_WAC CRS_DEP_TIME DEP_TIME DEP_DELAY DEP_DELAY_NEW DEP_DEL15 DEP_DELAY_GROUP DEP_TIME_BLK TAXI_OUT WHEELS_OFF WHEELS_ON TAXI_IN CRS_ARR_TIME ARR_TIME ARR_DELAY ARR_DELAY_NEW ARR_DEL15 ARR_DELAY_GROUP ARR_TIME_BLK CANCELLED CANCELLATION_CODE DIVERTED CRS_ELAPSED_TIME ACTUAL_ELAPSED_TIME AIR_TIME FLIGHTS DISTANCE DISTANCE_GROUP CARRIER_DELAY WEATHER_DELAY NAS_DELAY SECURITY_DELAY LATE_AIRCRAFT_DELAY FIRST_DEP_TIME TOTAL_ADD_GTIME LONGEST_ADD_GTIME DIV_AIRPORT_LANDINGS DIV_REACHED_DEST DIV_ACTUAL_ELAPSED_TIME DIV_ARR_DELAY DIV_DISTANCE DIV1_AIRPORT DIV1_AIRPORT_ID DIV1_AIRPORT_SEQ_ID DIV1_WHEELS_ON DIV1_TOTAL_GTIME DIV1_LONGEST_GTIME DIV1_WHEELS_OFF DIV1_TAIL_NUM DIV2_AIRPORT DIV2_AIRPORT_ID DIV2_AIRPORT_SEQ_ID DIV2_WHEELS_ON DIV2_TOTAL_GTIME DIV2_LONGEST_GTIME DIV2_WHEELS_OFF DIV2_TAIL_NUM DIV3_AIRPORT DIV3_AIRPORT_ID DIV3_AIRPORT_SEQ_ID DIV3_WHEELS_ON DIV3_TOTAL_GTIME DIV3_LONGEST_GTIME DIV3_WHEELS_OFF DIV3_TAIL_NUM DIV4_AIRPORT DIV4_AIRPORT_ID DIV4_AIRPORT_SEQ_ID DIV4_WHEELS_ON DIV4_TOTAL_GTIME DIV4_LONGEST_GTIME DIV4_WHEELS_OFF DIV4_TAIL_NUM DIV5_AIRPORT DIV5_AIRPORT_ID DIV5_AIRPORT_SEQ_ID DIV5_WHEELS_ON DIV5_TOTAL_GTIME DIV5_LONGEST_GTIME DIV5_WHEELS_OFF DIV5_TAIL_NUM year HourlyDryBulbTemperature HourlyDewPointTemperature HourlyRelativeHumidity HourlyAltimeterSetting HourlyVisibility HourlyStationPressure HourlyWetBulbTemperature HourlyPrecipitation HourlyCloudCoverage HourlyCloudElevation HourlyWindSpeed utc_timestamp CRS_DEP_MINUTES origin_delays_4h prev_flight_delay_in_minutes prev_flight_delay delay_origin_7d delay_origin_carrier_7d route delay_route_7d flight_count_24h LANDING_TIME_DIFF_MINUTES AVG_ARR_DELAY_ORIGIN AVG_TAXI_OUT_ORIGIN IS_HOLIDAY IS_HOLIDAY_WINDOW AIRPORT_HUB_CLASS RATING AIRLINE_CATEGORY dep_hour day_of_year dep_hour_sin dep_hour_cos dow_sin dow_cos doy_sin doy_cos HourlyVisibility_3h_change HourlyStationPressure_3h_change HourlyDryBulbTemperature_3h_change HourlyWindSpeed_3h_change HourlyPrecipitation_3h_change utc_ts_sec ground_flights_last_hour arrivals_last_hour xgb_predicted_delay time_idx hour SJU-2015-01-01-20409-262-N627JB-330 7.011568525186283E59 27 27 69.17473338802297 69.24446267432322 2 0.0010797446405919871 2.3847694827980768E-4 0.0 9.76930648451212 6.378967716607821 3.077932731747334 16.167910447761194 0.24036095159967186 1 1 1 4 2015-01-01 B6 20409 B6 N627JB 262 14843 1484304 34819 SJU San Juan, PR PR 72 Puerto Rico 3 10721 1072102 30721 BOS Boston, MA MA 25 Massachusetts 13 330 316 -14.0 0.0 0.0 -1 0001-0559 14.0 330 614 5.0 635 619 -16.0 0.0 0.0 -2 0600-0659 0.0 null 0.0 245.0 243.0 224.0 1.0 1674.0 7 null null null null null null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2015 77.09678082174158 72.0 85.0 30.109999999999996 10.0 30.100000000000005 74.0 0.0 4.0 45.0 0.5784970470518466 2015-01-01T03:30:00Z 210 0 -1.0 0 0.0 0.0 SJU-BOS 0.0 1 26.85 0.0 0.0 0 0 1 4.2 1 3.5 1.0 0.7933533402912352 0.6087614290087207 -0.433883739117558 -0.9009688679024191 0.017213356155834685 0.9998518392091162 null null null null null 1420083000 0 0 8.669572830200195 1 2015-01-01T03:00:00Z SJU-2015-01-01-20409-2276-N646JB-438 7.011568525186283E59 27 27 69.17473338802297 69.24446267432322 2 0.00107974464

### Calculate Number of Folds

Based on the configuration, we calculate how many complete folds fit within the dataset timespan.

In [0]:
# Get the maximum time index to determine dataset span
max_time_idx = df_indexed.agg(F.max("time_idx")).collect()[0][0]
print(f"Dataset spans {max_time_idx:,} unique hours")

# Extract configuration values
train_size = CV_CONFIG["train_hours"]
gap_size = CV_CONFIG["gap_hours"]
val_size = CV_CONFIG["val_hours"]
step_size = CV_CONFIG["step_hours"]

# Calculate total window size and number of folds
fold_window_size = train_size + gap_size + val_size
n_folds = (max_time_idx - fold_window_size) // step_size + 1

print(f"\nCross-Validation Configuration:")
print(f"  Training window:   {train_size:,} hours ({train_size // 24:,} days)")
print(f"  Gap size:          {gap_size} hours")
print(f"  Validation window: {val_size:,} hours ({val_size // 24:,} days)")
print(f"  Step size:         {step_size:,} hours")
print(f"  Total folds:       {n_folds}")

  Max time index: 33777
Step 2: Calculated 10 folds


In [0]:
# Generate fold assignments for each time index
# Each time index can belong to multiple folds (as train, gap, or validation)
fold_mapping = []

for fold_id in range(1, n_folds + 1):
    fold_start = 1 + (fold_id - 1) * step_size
    
    # Training period
    for t in range(fold_start, fold_start + train_size):
        fold_mapping.append((t, fold_id, "train"))
    
    # Gap period (excluded from both train and validation)
    for t in range(fold_start + train_size, fold_start + train_size + gap_size):
        fold_mapping.append((t, fold_id, "gap"))
    
    # Validation period
    for t in range(fold_start + train_size + gap_size, fold_start + train_size + gap_size + val_size):
        fold_mapping.append((t, fold_id, "validation"))

print(f"Generated {len(fold_mapping):,} fold assignments")

# Create DataFrame from fold mapping
fold_df = spark.createDataFrame(fold_mapping, ["time_idx", "fold_id", "split_type"])

# Join fold assignments with flight data
# Using broadcast join since fold_df is relatively small
result = df_indexed.join(
    F.broadcast(fold_df),
    on="time_idx",
    how="inner"
)

# Display fold statistics
print("\nRecords per fold and split type:")
result.groupBy("fold_id", "split_type").count().orderBy("fold_id", "split_type").display()


In [0]:
# =============================================================================
# Section 5: Export Splits
# =============================================================================

if SAVE_SPLITS:
    print(f"Saving CV splits to: {DATA_PATHS['output']}")
    
    # Write partitioned by fold_id and split_type for efficient loading
    result.write \
        .partitionBy("fold_id", "split_type") \
        .mode("overwrite") \
        .parquet(DATA_PATHS["output"])
    
    print("✓ CV splits saved successfully!")
else:
    print("SAVE_SPLITS is False. Set to True in configuration to enable saving.")
    print(f"Output path would be: {DATA_PATHS['output']}")

Careful! About to overwrite splits. If you want to continue, type y y

In [0]:
---

## Summary

This notebook generates time-based cross-validation splits for the flight delay prediction model. Key design decisions:

1. **Time-Based Splitting**: Prevents data leakage by ensuring training data always precedes validation data chronologically.

2. **Gap Period**: A 2-hour gap between training and validation prevents label leakage from flights that may have cascading delay effects.

3. **Sliding Window**: The step size creates overlapping folds, maximizing data utilization while maintaining temporal integrity.

4. **Partitioned Output**: Data is partitioned by `fold_id` and `split_type` for efficient loading during model training.

### Output Schema

The exported parquet files contain all original features plus:
- `time_idx`: Dense time index (hourly granularity)
- `fold_id`: Cross-validation fold identifier (1-10)
- `split_type`: "train", "gap", or "validation"